In [13]:
# import libraries
import cv2
import os
from PIL import Image
import datetime
import numpy as np
import datetime
import numpy as np
import math
import pandas as pd

In [11]:
def dni_rect_from_ce(x, y, cv2_v, img, areas_dict, lines_dict):
    w = img.shape[1]
    h = img.shape[0]

    color = (0, 0, 255)
    thicknes = 2

    fields = []
    res_dict = {}

    for key in areas_dict.keys():
        tras_vector = np.array([areas_dict[key]['tras_x'], areas_dict[key]['tras_y']])
        point = np.array([x, y]) + tras_vector
        point_2 = point + np.array([areas_dict[key]['width'], areas_dict[key]['height']])

        point = np.where(point<=0,0,point)
        point_2[0] = w if point_2[0] >= w else point_2[0]
        point_2[1] = h if point_2[1] >= h else point_2[1]

        cv2_v.rectangle(img,(point[0],point[1]),(point_2[0],point_2[1]),color,thicknes)
        res_dict[key] = (point, point_2)
        # print('{} {}'.format(point,point_2))

    for key in lines_dict.keys():
        tras_vector = np.array([lines_dict[key]['tras_x'], lines_dict[key]['tras_y']])
        point = np.array([x, y]) + tras_vector
        point_2 = point + np.array([lines_dict[key]['width'], lines_dict[key]['height']])

        point = np.where(point<=0,0,point)
        point_2[0] = w if point_2[0]>= w else point_2[0]
        point_2[1] = h if point_2[1]>= h else point_2[1]

        cv2_v.rectangle(img,(point[0],point[1]),(point_2[0],point_2[1]),color,thicknes)
        res_dict[key] = (point, point_2)

    return res_dict['dni'][0], res_dict['dni'][1], res_dict['tel'][0], res_dict['tel'][1]
    # return res_dict


In [78]:
dni_search_area = {
    'x_min':0,
    'x_max':833,
    'y_min':100,
    'y_max':190
}
traslation_dict = {
    'nomb_ape1':{'tras_x':215,'tras_y':-140,'width':480,'height':60},
    'nomb_ape2':{'tras_x':-40,'tras_y':-82,'width':730,'height':50},
    'dni':{'tras_x':27,'tras_y':-40,'width':300,'height':55},
    'tel':{'tras_x':27+400,'tras_y':-40,'width':270,'height':55},
    'dir1':{'tras_x':100,'tras_y':7,'width':595,'height':50},
    'dir2':{'tras_x':-40,'tras_y':57,'width':730,'height':50},
    'distrito':{'tras_x':70,'tras_y':102,'width':620,'height':50},
    'mail':{'tras_x':60,'tras_y':152,'width':635,'height':50},
    'cc':{'tras_x':200,'tras_y':198,'width':495,'height':50}
}
lines_dict = {
    'dni_tel':{'tras_x':-40,'tras_y':-40,'width':730,'height':55}
}

In [74]:
# SIFT initialization
detector = cv2.xfeatures2d.SIFT_create()
FLANN_INDEX_KDITREE = 0
flannParam = dict(algorithm=FLANN_INDEX_KDITREE, tree=5)
flann = cv2.FlannBasedMatcher(flannParam, {})
trainImg = cv2.imread("sift_img/dni5.jpg", 0)
trainKP, trainDesc = detector.detectAndCompute(trainImg, None)
MIN_MATCH_COUNT = 20

In [79]:
# 1 Getting files in multiple paths
# ruta = 'D:\\GyS\\proyectos\\cuponesWong\\proceso_definitivo\\escaneos_concursos'
ruta = 'C:\\git\\cuponesWong\\CuponesWong\\data\\escaneos\\camioneta_sonada_2018'
rutas_personas  = [arch.name for arch in os.scandir(ruta) if arch.is_dir()]
total = 0

files_lista = []

for persona in rutas_personas:
    bolsas  = [arch.name for arch in os.scandir(ruta + "\\" + persona) if arch.is_dir()]
    for bolsa in bolsas:
        files = [arch.name for arch in os.scandir(ruta + "\\" + persona + "\\" + bolsa) if arch.is_file()]
        for file in files:
            files_lista.append(ruta + "\\" + persona + "\\" + bolsa + "\\" + file)
print("Terminó. {}".format(len(files_lista)))

Terminó. 227646


In [75]:
# 1 Getting files from inputh
ruta = 'C:\\git\\cuponesWong\\CuponesWong\\notebooks_flow\\input'
files = [arch.name for arch in os.scandir(ruta) if arch.is_file()]
files_lista = []

for i in files:
    files_lista.append(ruta+'\\'+i)

print("Terminó. {}".format(len(files_lista)))

Terminó. 20


In [84]:
# Extracción del area de forma estática
y_min = dni_search_area['y_min']
y_max = dni_search_area['y_max']
x_min = dni_search_area['x_min']
x_max = dni_search_area['x_max']

INPUT = True
falses = 0

# array's
h_lista = []
w_lista = []
p_lista = []
c_x_lista = []
c_y_lista = []
file_lista = []
paths_lista = []

print("Inicio {}".format(datetime.datetime.now()))
# for filepath in files_lista[1730:1790]:
for filepath in files_lista[0::5]:
    # Initializing a boolean variable with False
    dni_founded = False

    if INPUT:
        print('Reading {}'.format(filepath))
        # Preprocessing section
        image = cv2.imread(filepath)
    else:
        print('Reading {}'.format(filepath[0]))
        # Preprocessing section
        image = cv2.imread(filepath[0])

    # print('Reading {}'.format(filepath))
    gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    # print('{}'.format(image.shape))
    y_max = image.shape[0] if y_max > image.shape[0] else y_max
    x_max = image.shape[1] if x_max > image.shape[1] else x_max

    sift_roi = gray[y_min:y_max, x_min:x_max]
    sift_roi = cv2.adaptiveThreshold(sift_roi, 255, cv2.ADAPTIVE_THRESH_GAUSSIAN_C, cv2.THRESH_BINARY, 21, 11)
    
    # SIFT DETECTION
    queryKP, queryDesc = detector.detectAndCompute(sift_roi, None)
    matches = flann.knnMatch(queryDesc, trainDesc, k=2)
    detection = False

    goodMatch = []
    for m, n in matches:
        if(m.distance < 0.75 * n.distance):
            goodMatch.append(m)
    if(len(goodMatch) > MIN_MATCH_COUNT):
        tp = []
        qp = []
        for m in goodMatch:
            tp.append(trainKP[m.trainIdx].pt)
            qp.append(queryKP[m.queryIdx].pt)
        tp, qp = np.float32((tp, qp))
        H, status = cv2.findHomography(tp, qp, cv2.RANSAC, 3.0)
        h, w = trainImg.shape
        trainBorder = np.float32([[[0, 0], [0, h-1], [w-1, h-1], [w-1, 0]]])
        queryBorder = cv2.perspectiveTransform(trainBorder, H)
        cv2.polylines(sift_roi, [np.int32(queryBorder)], True, (0, 255, 0), 2)
        dni_founded = True
        
    if dni_founded:
        # -------Comparacion de Hmax y Wmax-----
        # restringinedo valores a 0
        queryBorder = np.where(queryBorder < 0, 0, queryBorder)

        # Coordenadas "query"
        x0 = queryBorder[[[0],0]][[0],0]
        y0 = queryBorder[[[0],0]][[0],1]

        x1 = queryBorder[[[0],1]][[0],0]
        y1 = queryBorder[[[0],1]][[0],1]

        x2 = queryBorder[[[0],2]][[0],0]
        y2 = queryBorder[[[0],2]][[0],1]

        x3 = queryBorder[[[0],3]][[0],0]
        y3 = queryBorder[[[0],3]][[0],1]

        arr_x = np.array([x0, x1, x2, x3])
        x_maximo = arr_x.max()
        x_minimo = arr_x.min()
        c_x = int(arr_x.sum() / arr_x.size)

        arr_y = np.array([y0, y1, y2, y3])
        y_maximo = arr_y.max()
        y_minimo = arr_y.min()
        c_y = int(arr_y.sum() / arr_y.size)

        h_lista.append(y_maximo - y_minimo)
        w_lista.append(x_maximo - x_minimo)
        p_lista.append([(x0, y0), (x1, y1), (x2, y2), (x3, y3)])
        c_x_lista.append(c_x)
        c_y_lista.append(c_y)
        paths_lista.append(filepath if INPUT else filepath[0])
    else:
        falses += 1
        h_lista.append(9999)
        w_lista.append(9999)
        p_lista.append([(0,0,),(0,0,),(0,0,),(0,0,)])
        c_x_lista.append(9999)
        c_y_lista.append(9999)
        paths_lista.append(filepath if INPUT else filepath[0])

    # cv2.imshow("image", image)
    # cv2.imshow("sift_roi", sift_roi)
    # cv2.waitKey(0)
    # cv2.destroyAllWindows()

# convirtiendo a nunmpy arrays
n_widths = np.array(w_lista)
n_heights = np.array(h_lista)
n_points = np.array(p_lista)
n_cxs = np.array(c_x_lista)
n_cys = np.array(c_y_lista)
n_paths = np.array(paths_lista)

data = {
    'path': n_paths,
    'width': n_widths,
    'height': n_heights,
    'cx': n_cxs,
    'cy': n_cys
}
areas_r = pd.DataFrame(data)
areas_r.to_csv('areas_result/areas.csv', index=False)
print("Termino :D {} Total de falses: {}".format(datetime.datetime.now(), falses))

Inicio 2019-11-10 19:47:38.812436
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152351_00001.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152351_00006.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152351_00011.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152351_00016.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152351_00021.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152351_00026.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152352_00031.jpg
Reading C:\git\cuponesWong\C

Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152359_00321.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152400_00326.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152400_00331.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152400_00336.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152400_00341.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152400_00346.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152400_00351.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta

Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152408_00641.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152408_00646.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152409_00651.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152409_00656.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152409_00661.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152409_00666.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152409_00671.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta

Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152418_00956.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152419_00961.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152419_00966.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152419_00971.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152419_00976.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152419_00981.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814152419_00986.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta

Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814154635_00276.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814154635_00281.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814154635_00286.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814154635_00291.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814154635_00296.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814154635_00301.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\AV\B37\CamionetaToyota2018_AV_B37_20190814154635_00306.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta

...

Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827160349_00432.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827160349_00437.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827160349_00442.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827160350_00447.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827160351_00452.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827160351_00457.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827160352_00462.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta

Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827160408_00747.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827160408_00752.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827160408_00757.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827160408_00762.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827160409_00767.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827160409_00772.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827160409_00777.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta

Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162626_00062.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162626_00067.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162626_00072.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162626_00077.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162627_00082.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162627_00087.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162628_00092.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta

Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162643_00377.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162643_00382.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162644_00387.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162644_00392.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162645_00397.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162645_00402.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162645_00407.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta

Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162704_00687.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162704_00692.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162704_00697.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162705_00702.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162705_00707.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162705_00712.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta_sonada_2018\MD\B45\CamionetaToyota2018_MD_B45_20190827162706_00717.jpg
Reading C:\git\cuponesWong\CuponesWong\data\escaneos\camioneta

In [82]:
falses

0

In [77]:
# for i in range(m_files.size):
for i in range(areas_r.path.values.size):
    # Grabbing the file
    filename = areas_r.path.values[i]
    name = filename.split('\\')
    name = name[len(name) - 1]
    name = name.split('.')[0]

    c_x = int(areas_r.cx.values[i])
    c_y = int(areas_r.cy.values[i])

    wi = areas_r.width.values[i]
    hi = areas_r.height.values[i]

    x_minimo = int(c_x - (wi / 2))
    x_maximo = int(c_x + (wi / 2))
    y_minimo = int(c_y - (hi / 2))
    y_maximo = int(c_y + (hi / 2))

    image = cv2.imread(filename)
    frame = image.copy()
    found = False

    if (c_x == 9999 or c_y == 9999):
        # cv2.putText(image,'{}'.format('Area no detectada'), (25, 25), cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0, 0, 255), 2)
        print('{},{}'.format(filename, 'Ancla no encontrada'))
        found = False
    else:
        found = True
        print('{} . {}'.format(i, name))
        cv2.rectangle(image,(x_minimo, y_minimo + int(y_min)), (x_maximo,y_maximo+int(y_min)), (0,0,255), 1)
        dni_rect_from_ce(c_x, c_y + y_min, cv2, image, traslation_dict, {})
        
    cv2.imshow("Img", image)
    cv2.waitKey(0)
    cv2.destroyAllWindows()


0 . CamionetaToyota2018_AV_B37_20190815112050_00738
1 . CamionetaToyota2018_AV_B37_20190815112050_00741
2 . CamionetaToyota2018_AV_B37_20190815112051_00744
3 . CamionetaToyota2018_AV_B37_20190815112051_00747
4 . CamionetaToyota2018_AV_B37_20190815112051_00750
5 . CamionetaToyota2018_AV_B37_20190815112051_00767
6 . CamionetaToyota2018_AV_B37_20190815112051_00770
